# Analyse, classification et indexation des données: feuille 9
### Apprentissage supervisé, Arbres de décision et Forêts aléatoires

## Avant propos

Dans cette feuille, nous allons étudier une catégorie d'algorithmes d'apprentissage supervisé différente de ce que nous avons vu jusque là : 

- les arbres de décisions ont cela de particulier qu'ils sont construits en utilisant des éléments de la théorie de l'information. Leur utilisation, ensuite, est assez facilement implémentable par des règles Si-Sinon simples. 

- les forêts aléatoires implémentent, elles, une approche de bagging.

In [ ]:
import numpy as np
import pandas as pa
import warnings
warnings.filterwarnings("ignore")

### Exercice 1. Arbres de décision (à la main)

Dans ce premier exercice, nous allons écrire un ensemble de fonctions implémentant les éléments vus en cours et permettant de construire un arbre de décision.  

Pour vérifier vos fonctions, vous pouvez les appliquer à l'exemple très simple vu en cours :


In [ ]:
exemple_cours = pa.DataFrame(data={'A': [0, 0, 1, 1],
                                  'B': [1, 0, 1, 0],
                                  'Classe': ['C1', 'C1', 'C2', 'C2']})

1- Ecrire une fonction <code>information(dataset, label_feature)</code> permettant de calculer la quantité d'information nécessaire pour classifier un élément du corpus <code>dataset</code>. Le paramètre <code>label_feature</code> indique la colonne contenant les classes des éléments.

In [ ]:
### CORRECTION
def information(dataset, label_feature):
    l = np.unique(dataset[label_feature])
    p = [len(dataset[dataset[label_feature]==l[i]]) for i in range(len(l))]
    I = np.sum(np.multiply(-1, p * np.log2(p/(np.sum(p)))))
    return I
    
print(information(exemple_cours, 'Classe'))

2- Ecrire une fonction <code>entropy(dataset, feature, label_feature)</code> calculant l'entropie du descripteur <code>feature</code>

In [ ]:
### CORRECTION
def entropy(dataset, feature, label_feature):
    val_feature = np.unique(dataset[feature])
    data = {}
    for i in range(len(val_feature)):
        data[i] = dataset[dataset[feature] == val_feature[i]]
    
    
    e = 0
    for i in range(len(data)):
        e += information(data[i], label_feature)
    return e
    
        

print('Entropy(A): ', entropy(exemple_cours, 'A', 'Classe'))
print('Entropy(B): ', entropy(exemple_cours, 'B', 'Classe'))




3- Ecrire une fonction <code>gain(dataset, feature, label_feature)</code> calculant le gain d'information obtenu en choisissant le descripteur <code>feature</code> pour partitionner le corpus <code>dataset</code>

In [ ]:
### CORRECTION
def gain(dataset, feature, label_feature):
    return information(dataset, label_feature) - entropy(dataset, feature, label_feature)

print('Gain(A): ', gain(exemple_cours, 'A', 'Classe'))
print('Gain(B): ', gain(exemple_cours, 'B', 'Classe'))

4- En vous aidant des fonctions que vous avez écrites ci-dessus, construisez l'arbre de décision pour prédire Achat avec le corpus suivant. On ne demande pas d'écrire un programme qui construit l'arbre mais plutôt d'utiliser les fonctions pour faire les calculs à votre place.

\begin{array}{|c|c|c|c|c|}
\hline
\hline
Sexe & Age & Etat civil & Revenu & Achat \\
\hline
Homme & 18-35   & Marie       & Moyen  & Non \\
Homme & <18     & Celibataire & Faible & Non \\
Homme & >35     & Marie       & Eleve  & Oui \\
Femme & <18     & Celibataire & Moyen  & Non \\
Homme & 18 - 35 & Celibataire & Moyen  & Non \\
Femme & 18 - 35 & Celibataire & Eleve  & Oui \\
Femme & 18 - 35 & Marie       & Faible & Non \\
Homme & 18 - 35 & Marie       & Eleve  & Oui \\
Homme & >35     & Celibataire & Faible & Oui \\
Femme & <18     & Celibataire & Moyen  & Non \\
Femme & >35     & Celibataire & Moyen  & Oui \\
Femme & >35     & Marie       & Eleve  & Oui \\
Homme & 18 - 35 & Celibataire & Faible & Non\\
Femme & 18 - 35 & Marie       & Moyen  & Oui\\
\hline
\hline
\end{array}

In [ ]:
dataset = pa.DataFrame(data={'Sexe': ['Homme', 'Homme', 'Homme', 'Femme','Homme', 'Femme', 'Femme', 
                                'Homme', 'Homme', 'Femme', 'Femme', 'Femme','Homme', 'Femme'],
                      'Age': ['18-35', '<18', '>35', '<18', '18-35', '18-35', '18-35', '18-35', 
                              '>35', '<18', '>35', '>35', '18-35', '18-35'],
                      'Etat_civil': ['marie', 'celibataire', 'marie', 'celibataire', 'celibataire', 
                                     'celibataire', 'marie', 'marie', 'celibataire', 'celibataire',
                                    'celibataire', 'marie', 'celibataire', 'marie'],
                      'Revenu': ['Moyen', 'Faible', 'Eleve', 'Moyen', 'Moyen', 'Eleve', 'Faible',
                                'Eleve', 'Faible', 'Moyen', 'Moyen', 'Eleve', 'Faible', 'Moyen'],
                      'Achat': ['Non', 'Non', 'Oui', 'Non', 'Non', 'Oui', 'Non', 'Oui', 'Oui', 'Non',
                               'Oui', 'Oui', 'Non', 'Oui']})
#dataset

In [ ]:
### CORRECTION
gains = {}
features = dataset.columns.drop('Achat')
for f in features:
    gains[f] = gain(dataset, f, 'Achat')
    
gains

In [ ]:
### CORRECTION
# Le plus grand gain vient de Age, on choisit ce descripteur pour partitionner le corpus
dataset1 = dataset[dataset['Age']=='<18']
dataset2 = dataset[dataset['Age']=='18-35']
dataset3 = dataset[dataset['Age']=='>35']

In [ ]:
### CORRECTION
# Y a-t-il un noeud homogène?
print(np.unique(dataset1['Achat']))
print(np.unique(dataset2['Achat']))
print(np.unique(dataset3['Achat']))

In [ ]:
### CORRECTION
# Seul le noeud avec Age=18-35 n'est pas homogène. On doit donc continuer le partitionnement sur ce noeud :
gains = {}
features = dataset2.columns.drop('Achat')
for f in features:
    gains[f] = gain(dataset2, f, 'Achat')
    
gains

In [ ]:
### CORRECTION
#Le plus grand gain vient de Revenu, on choisit ce descripteur pour partitionner le noeud
dataset21 = dataset2[dataset2['Revenu']=='Faible']
dataset22 = dataset2[dataset2['Revenu']=='Moyen']
dataset23 = dataset2[dataset2['Revenu']=='Eleve']

In [ ]:
### CORRECTION
# Est-ce qu'on a encore du désordre ?
print(np.unique(dataset21['Achat']))
print(np.unique(dataset22['Achat']))
print(np.unique(dataset23['Achat']))

In [ ]:
### CORRECTION
#Le noeud avec Revenu=Moyen n'est pas homogène. On doit donc continuer le partitionnement sur ce noeud :
gains = {}
features = dataset22.columns.drop('Achat')
for f in features:
    gains[f] = gain(dataset22, f, 'Achat')
    
gains

In [ ]:
### CORRECTION
#L’attribut Sexe donne le meilleur gain d’entropie et on choisit celui-ci pour séparer les exemples
dataset221 = dataset22[dataset22['Sexe']=='Homme']
dataset222 = dataset22[dataset22['Sexe']=='Femme']

In [ ]:
### CORRECTION
#Est-ce qu'on a encore du désordre ? Non, cest fini!
print(np.unique(dataset221['Achat']))
print(np.unique(dataset222['Achat']))

5- Dessiner l'arbre de décision obtenu.

### CORRECTION
Age < 18 -->  Achat=Non

Age dans 18 - 35 : 

    - Revenu = Faible -->  Achat=Non
    
    - Revenu = Moyen :
        - Sexe = Homme -->  Achat = Non
        
        - Sexe =Femme --> Achat =Oui
        
    - Revenu = Elevé : Achat=Oui
Age > 35 --> Achat = Oui

## Exercice 2. Arbres de décision avec <code>sklearn</code>

Dans cet exercice, nous allons utiliser la bibliothèque <code>sklearn</code> pour entraîner et tester un arbre de décision. 

Pour cela, nous allons utiliser le corpus <code>titanic.csv</code>. Un échantillon de ce corpus est diponible à l'adresse : 

https://www.labri.fr/perso/zemmari/datasets/titanic.csv

Une description détaillée de ce corpus et des descripteurs le composant peut être consultée à l'adresse :

https://www.kaggle.com/c/titanic/data

On vous laisse découvrir la tragédie à laquelle est lié ce corpus :-)


1- Chargez le corpus et explorez son contenu.

In [ ]:
### CORRECTION
dataset = pa.read_csv('https://www.labri.fr/perso/zemmari/datasets/titanic.csv')
dataset.head()

In [ ]:
### CORRECTION
dataset.info()

2- Supprimez les lignes contenant des données manquantes

In [ ]:
### CORRECTION
dataset.dropna(inplace=True)
dataset.info()

3- On souhaite construire un modèle pour prédire, pour un passager, s'il survivra ou non. Supprimez les descripteurs qui ne vous paraissent pas pertinents pour la prédiction. Expliquez vos choix.

In [ ]:
### CORRECTION
dataset = dataset[['Pclass', 'Sex', 'Age', 'SibSp', 'Parch', 'Fare', 'Embarked', 'Survived']]
dataset.info()

4- La cellule suivante permet de convertir une catégorie au format entier ou au format texte en un entier. 
Exécutez la telle quelle et observez son résultat.

In [ ]:
from sklearn import preprocessing

cols = ['Sex', 'Embarked']
le = preprocessing.LabelEncoder()
for c in cols:
    le.fit(dataset[c])
    dataset[c] = le.transform(dataset[c])
dataset

5- Séparez les données en un ensemble $X$ contenant les variables explicatives et $y$ la variable à prédire.

In [ ]:
### CORRECTION
X = dataset[['Pclass', 'Sex', 'Age', 'SibSp', 'Parch', 'Fare', 'Embarked']]
y = dataset['Survived']

6- Partitionnez les données en ensemble d'entraînement et de test

In [ ]:
### CORRECTION
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=.3, random_state=109)

7- Instanciez un classifieur Decision Tree et entraînez-le avec les données d'entraînement.

In [ ]:
### CORRECTION
from sklearn import tree
dt = tree.DecisionTreeClassifier()
dt.fit(X_train, y_train)

8- Visualisez l'arbre obtenu. Décommentez/complétez pour cela le code suivant

In [ ]:
#from sklearn.tree import export_graphviz
#from six import StringIO  
#from IPython.display import Image  
#import pydotplus

#features_cols = ...
#class_names=['0','1']

#dot_data = StringIO()
#export_graphviz(dt, out_file=dot_data,  
#                filled=True, rounded=True,
#                special_characters=True,feature_names = features_cols,class_names=class_names)
#graph = pydotplus.graph_from_dot_data(dot_data.getvalue())  
#graph.write_png('titanic.png')
#Image(graph.create_png())

In [ ]:
### CORRECTION
from sklearn.tree import export_graphviz
from six import StringIO  
from IPython.display import Image  
import pydotplus

features_cols = ['Pclass', 'Sex', 'Age', 'SibSp', 'Parch', 'Fare', 'Embarked']
class_names=['0','1']

dot_data = StringIO()
export_graphviz(dt, out_file=dot_data,  
                filled=True, rounded=True,
                special_characters=True,feature_names = features_cols,class_names=class_names)
graph = pydotplus.graph_from_dot_data(dot_data.getvalue())  
#graph.write_png('titanic.png')
Image(graph.create_png())

9- Mesurez la qualité de votre classifieur.

In [ ]:
### CORRECTION
from sklearn import metrics
y_pred = dt.predict(X_test)
scores = metrics.accuracy_score(y_test, y_pred)
print('Accuracy: ','{:2.2%}'.format(scores))

10- Changez les valeurs par défaut des différents paramètres et observez la qualité de votre classifieur. 

In [ ]:
### CORRECTION
dt

In [ ]:
### CORRECTION
criterion = ['gini', 'entropy']
max_depth = [3, 5, 10]
min_samples_leaf = [1, 2, 5]
min_samples_split = [2, 3, 4]

best_params = None#[criterion[0], max_depth[0], min_samples_leaf[0], min_samples_split[0]]
best_score = 0
for c in criterion:
    for depth in max_depth:
        for l in min_samples_leaf:
            for s in min_samples_split:
                dt = tree.DecisionTreeClassifier(criterion=c, max_depth=depth, 
                                                 min_samples_leaf=l, min_samples_split=s)
                dt.fit(X_train, y_train)
                y_pred = dt.predict(X_test)
                scores = metrics.accuracy_score(y_test, y_pred)
                if best_score==0 or scores > best_score:
                    best_score = scores
                    best_params = [c, depth, l, s]

print('Best Accuracy: ','{:2.2%}'.format(best_score))
print('Parameters: ', best_params)

                

## Exercice 3. Random forest

Quelles sont les performances d'un classifieur de type forêts aléatoires sur le même corpus que l'exercice précédant ?



In [ ]:
### CORRECTION
from sklearn.ensemble import RandomForestClassifier
rf = RandomForestClassifier()
rf.fit(X_train, y_train)
y_pred = rf.predict(X_test)
scores = metrics.accuracy_score(y_test, y_pred)
print('Accuracy: ','{:2.2%}'.format(scores))

Cherchez le meilleur paramètrage pour le meilleur classifieur en complétant / décommentant le code suivant.

In [ ]:
# from sklearn.model_selection import RandomizedSearchCV
# Number of trees in random forest
# n_estimators = ...
# Number of features to consider at every split
# max_features = ...
# Maximum number of levels in tree
# max_depth = ...
# Minimum number of samples required to split a node
# min_samples_split = ...
# Minimum number of samples required at each leaf node
# min_samples_leaf = ...
# Method of selecting samples for training each tree
# bootstrap = ...
# Create the random grid
#random_grid = {'n_estimators': n_estimators,
#               'max_features': max_features,
#               'max_depth': max_depth,
#               'min_samples_split': min_samples_split,
#               'min_samples_leaf': min_samples_leaf,
#              'bootstrap': bootstrap}
#print(random_grid)

In [ ]:
### CORRECTION
from sklearn.model_selection import RandomizedSearchCV
# Number of trees in random forest
n_estimators = [int(x) for x in np.linspace(start = 200, stop = 2000, num = 10)]
# Number of features to consider at every split
max_features = [None, 'sqrt']
# Maximum number of levels in tree
max_depth = [int(x) for x in np.linspace(10, 110, num = 11)]
max_depth.append(None)
# Minimum number of samples required to split a node
min_samples_split = [2, 5, 10]
# Minimum number of samples required at each leaf node
min_samples_leaf = [1, 2, 4]
# Method of selecting samples for training each tree
bootstrap = [True, False]
# Create the random grid
random_grid = {'n_estimators': n_estimators,
               'max_features': max_features,
               'max_depth': max_depth,
               'min_samples_split': min_samples_split,
               'min_samples_leaf': min_samples_leaf,
               'bootstrap': bootstrap}
print(random_grid)

In [ ]:
# Use the random grid to search for best hyperparameters
# First create the base model to tune
rf = RandomForestClassifier()
# Random search of parameters, using 3 fold cross validation, 
# search across 100 different combinations, and use all available cores
rf_random = RandomizedSearchCV(estimator = rf, param_distributions = random_grid, n_iter = 100, 
                               cv = 3, verbose=2, random_state=42, n_jobs = -1)
rf_random.fit(X_train, y_train)

In [ ]:
rf_random.best_params_

In [ ]:
### CORRECTION
best_rf = RandomForestClassifier(bootstrap=True,
                                 max_depth=80,
                                 max_features='sqrt',
                                 min_samples_leaf=4,
                                 min_samples_split=5,
                                 n_estimators=1000)


best_rf.fit(X_train, y_train)
y_pred = best_rf.predict(X_test)
scores = metrics.accuracy_score(y_test, y_pred)
print('Accuracy: ','{:2.2%}'.format(scores))